In [1]:
import pandas as pd
import numpy as np

In [2]:
dy3 = pd.read_csv('C:/Master/yellow_tripdata_2015-03_2.csv')

In [3]:
dy3.head()

VendorID tpep_pickup_datetime tpep_dropoff_datetime  passenger_count  \
0         1  2015-03-06 08:02:31   2015-03-06 08:09:55                1   
1         1  2015-03-06 08:02:31   2015-03-06 08:15:23                1   
2         1  2015-03-06 08:02:31   2015-03-06 08:12:27                1   
3         1  2015-03-06 08:02:31   2015-03-06 08:09:09                1   
4         1  2015-03-06 08:02:32   2015-03-06 08:19:37                1   

   trip_distance  pickup_longitude  pickup_latitude  RateCodeID  \
0            1.2        -73.990211        40.750969           1   
1            3.2        -73.935188        40.800720           1   
2            1.1        -73.963753        40.767937           1   
3            0.8        -73.997177        40.742168           1   
4            2.7        -74.006844        40.730267           1   

  store_and_fwd_flag  dropoff_longitude  dropoff_latitude  payment_type  \
0                  N         -73.987892         40.738037             2   
1                  N         -73.952553         40.765373             2   
2                  N         -73.956947         40.780270             2   
3                  N         -74.008064         40.739281             1   
4                  N         -73.976860         40.750671             1   

   fare_amount  extra  mta_tax  tip_amount  tolls_amount  \
0          7.0    0.0      0.5        0.00           0.0   
1         11.5    0.0      0.5        0.00           0.0   
2          8.0    0.0      0.5        0.00           0.0   
3          6.0    0.0      0.5        1.00           0.0   
4         13.0    0.0      0.5        2.75           0.0   

   improvement_surcharge  total_amount  
0                    0.3          7.80  
1                    0.3         12.30  
2                    0.3          8.80  
3                    0.3          7.80  
4                    0.3         16.55

# Visualizamos

In [4]:
import datashader as ds
from datashader import transfer_functions as tr_fns
from datashader.colors import Greys9
Greys9_r = list(reversed(Greys9))[:2]

In [5]:
from bokeh.plotting import figure, output_notebook, show
output_notebook()

Loading BokehJS ...

In [6]:
NYC = x_range, y_range = ((-75.00, -73.0), (40.0, 41.0))

plot_width = int(750)
plot_height = int(plot_width//1.2)

In [7]:
def base_plot(tools='pan, wheel_zoom, reset', plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
              x_range=x_range, y_range=y_range, outline_line_color=None,
              min_border=0, min_border_left=0, min_border_right=0,
              min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

In [8]:
ejemplo = dy3.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='blue', size=5)

p.circle(x=ejemplo['pickup_longitude'], y=ejemplo['pickup_latitude'], **options)
show(p)

In [9]:
ejemplo = dy3.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='red', size=5)

p.circle(x=ejemplo['dropoff_longitude'], y=ejemplo['dropoff_latitude'], **options)
show(p)

# Visualización con HeatMap

In [10]:
from datashader.bokeh_ext import InteractiveImage
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno
from IPython.core.display import HTML, display

background = "black"
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="black"))

In [11]:
def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(dy3, 'dropoff_longitude', 'dropoff_latitude', ds.count('passenger_count'))
    img = tr_fns.shade(agg, cmap=Hot, how='eq_hist')
    return tr_fns.dynspread(img, threshold=0.5, max_px=4)

p = base_plot(background_fill_color=background)
export(create_image(*NYC), "NYCABs")
InteractiveImage(p, create_image)

In [12]:
def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(dy3, 'pickup_longitude', 'pickup_latitude', ds.count('passenger_count'))
    img = tr_fns.shade(agg, cmap=Hot, how='eq_hist')
    return tr_fns.dynspread(img, threshold=0.5, max_px=4)

p = base_plot(background_fill_color=background)
export(create_image(*NYC), "NYCABs_Recoger")
InteractiveImage(p, create_image)

Indicar que no vemos diferencias entre meses 03 y 04, observamos que hay diferencias entre zonas de recogida y dejar pasaje, este tipo de taxis, tiene como preferencia la zona del bajo Manhattan.

Observamos que la zona de recogida preferida son los barrios del bajo Manhattan, con una fuerte presencia.

Observamos que este tipo de taxis recoge pasaje en los aeropuertos, tanto JFK, la Guardia y New Yersey. Siendo especialmente fuerte la recogida en JFK y La Guardia, menor en New Jersey.

Dejar pasaje, es fuerte la presencia en los tres aeropuertos, la zona de bajo Manhattan tiene mucho servicios a estos.

Hemos observado que usando la libreria datashader se realiza una buena visualización de mapa de calor, realizando una cartografia muy buena del terreno, con fuerte luz en las zonas de mas influencia, es una buena libreria a tener presente para datos con coordenadas de geolocalización.
